In [27]:
from scripts.scraping import scrape_symbols, scrape_financial, download_data
import pandas as pd
import os

In [28]:
FIRST_RUN = False
cotation_url = ['https://www.slickcharts.com/sp500']
pd.options.display.max_columns = None

In [29]:
if FIRST_RUN:
    if 'data' not in os.listdir('..'):
        os.mkdir('../data')
    if 'symbols.txt' not in os.listdir('../data'):
        with open('../data/symbols.txt', 'w') as f:
            pass
    if 'financials' not in os.listdir('..'):
        os.mkdir('../data/financials')
    if 'links.txt' not in os.listdir('../data'):
        with open('../data/links.txt', 'w') as f:
            pass
    symbols = scrape_symbols(cotation_url, '../data/symbols.txt')
else:
    with open('../data/symbols.txt', 'r') as f:
        symbols = f.readlines()
        symbols = [symbol.strip() for symbol in symbols]

In [5]:
links = scrape_financial(symbols, progress_file='../data/links.txt')

In [ ]:
download_data('../data/links.txt')

In [30]:
#Models
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler
import pandas as pd
from tqdm import tqdm

In [5]:
def dataset_preparation():
    data = pd.read_csv('../data/financials.csv')
    dict_df = {}
    for symbol in tqdm(data['Symbol'].unique(), desc='Processing data'):
        dict_df[symbol] = data[data['Symbol'] == symbol][['Symbol', 'Date', 'Open', 'High', 'Low', 'Close', 'Adj Close', 'Volume']]
    return dict_df

dict_df = dataset_preparation()

Processing data: 100%|██████████| 501/501 [01:22<00:00,  6.07it/s]


In [31]:
#Merge all dataframes on the date column and add suffixes to the columns
merged_df = pd.DataFrame()
for symbol in tqdm(dict_df.keys(), desc='Merging dataframes'):
    if merged_df.empty:
        merged_df = dict_df[symbol]
    else:
        merged_df = pd.merge(merged_df, dict_df[symbol], on='Date', suffixes=('', f'_{symbol}'), how='outer')

Merging dataframes: 100%|██████████| 501/501 [02:02<00:00,  4.08it/s]


In [33]:
merged_df['Date'] = pd.to_datetime(merged_df['Date'])
merged_df.head()

Symbol       Date  Open  High  Low  Close  Adj Close  Volume Symbol_AAL  \
0    NaN 1962-01-02   NaN   NaN  NaN    NaN        NaN     NaN        NaN   
1    NaN 1962-01-03   NaN   NaN  NaN    NaN        NaN     NaN        NaN   
2    NaN 1962-01-04   NaN   NaN  NaN    NaN        NaN     NaN        NaN   
3    NaN 1962-01-05   NaN   NaN  NaN    NaN        NaN     NaN        NaN   
4    NaN 1962-01-08   NaN   NaN  NaN    NaN        NaN     NaN        NaN   

   Open_AAL  High_AAL  Low_AAL  Close_AAL  Adj Close_AAL  Volume_AAL  \
0       NaN       NaN      NaN        NaN            NaN         NaN   
1       NaN       NaN      NaN        NaN            NaN         NaN   
2       NaN       NaN      NaN        NaN            NaN         NaN   
3       NaN       NaN      NaN        NaN            NaN         NaN   
4       NaN       NaN      NaN        NaN            NaN         NaN   

  Symbol_AAPL  Open_AAPL  High_AAPL  Low_AAPL  Close_AAPL  Adj Close_AAPL  \
0         NaN        NaN        NaN       NaN         NaN             NaN   
1         NaN        NaN        NaN       NaN         NaN             NaN   
2         NaN        NaN        NaN       NaN         NaN             NaN   
3         NaN        NaN        NaN       NaN         NaN             NaN   
4         NaN        NaN        NaN       NaN         NaN             NaN   

   Volume_AAPL Symbol_ABBV  Open_ABBV  High_ABBV  Low_ABBV  Close_ABBV  \
0          NaN         NaN        NaN        NaN       NaN         NaN   
1          NaN         NaN        NaN        NaN       NaN         NaN   
2          NaN         NaN        NaN        NaN       NaN         NaN   
3          NaN         NaN        NaN        NaN       NaN         NaN   
4          NaN         NaN        NaN        NaN       NaN         NaN   

   Adj Close_ABBV  Volume_ABBV Symbol_ABNB  Open_ABNB  High_ABNB  Low_ABNB  \
0             NaN          NaN         NaN        NaN        NaN       NaN   
1             NaN          NaN         NaN        NaN        NaN       NaN   
2             NaN          NaN         NaN        NaN        NaN       NaN   
3             NaN          NaN         NaN        NaN        NaN       NaN   
4             NaN          NaN         NaN        NaN        NaN       NaN   

   Close_ABNB  Adj Close_ABNB  Volume_ABNB Symbol_ABT  Open_ABT  High_ABT  \
0         NaN             NaN          NaN        NaN       NaN       NaN   
1         NaN             NaN          NaN        NaN       NaN       NaN   
2         NaN             NaN          NaN        NaN       NaN       NaN   
3         NaN             NaN          NaN        NaN       NaN       NaN   
4         NaN             NaN          NaN        NaN       NaN       NaN   

   Low_ABT  Close_ABT  Adj Close_ABT  Volume_ABT Symbol_ACGL  Open_ACGL  \
0      NaN        NaN            NaN         NaN         NaN        NaN   
1      NaN        NaN            NaN         NaN         NaN        NaN   
2      NaN        NaN            NaN         NaN         NaN        NaN   
3      NaN        NaN            NaN         NaN         NaN        NaN   
4      NaN        NaN            NaN         NaN         NaN        NaN   

   High_ACGL  Low_ACGL  Close_ACGL  Adj Close_ACGL  Volume_ACGL Symbol_ACN  \
0        NaN       NaN         NaN             NaN          NaN        NaN   
1        NaN       NaN         NaN             NaN          NaN        NaN   
2        NaN       NaN         NaN             NaN          NaN        NaN   
3        NaN       NaN         NaN             NaN          NaN        NaN   
4        NaN       NaN         NaN             NaN          NaN        NaN   

   Open_ACN  High_ACN  Low_ACN  Close_ACN  Adj Close_ACN  Volume_ACN  \
0       NaN       NaN      NaN        NaN            NaN         NaN   
1       NaN       NaN      NaN        NaN            NaN         NaN   
2       NaN       NaN      NaN        NaN            NaN         NaN   
3       NaN       NaN      NaN        NaN            NaN  

In [47]:
symbol_df = merged_df[[col for col in merged_df.columns if 'Symbol' or 'Date' in col]]

In [54]:
#Supprimer les lignes où la proportion de nan est supérieure à 0.5
symbol_df = symbol_df.dropna(thresh=0.9*len(symbol_df.columns), axis=0)
merged_df = merged_df.dropna(thresh=0.9*len(merged_df.columns), axis=0)

In [55]:
symbol_df['Date'].dt.date.min(), symbol_df['Date'].dt.date.max(), symbol_df['Date'].dt.date.max() - symbol_df['Date'].dt.date.min(), symbol_df['Date'].dt.date.unique().shape

(datetime.date(2012, 3, 30),
 datetime.date(2024, 4, 17),
 datetime.timedelta(days=4401),
 (3031,))

In [58]:
merged_df.isna().sum().sum()

380590

In [72]:
#Fill the missing values for each column with the closest value in the past
test = merged_df.fillna(method='bfill')
test.isna().sum().sum()

C:\Users\kamen\AppData\Local\Temp\ipykernel_19048\14627872.py:2: FutureWarning: DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  test = merged_df.fillna(method='bfill')


0

In [73]:
test

Symbol       Date        Open        High         Low       Close  \
12649      A 2012-03-30   32.017166   32.088699   31.473534   31.838341   
12650      A 2012-04-02   31.838341   32.267525   31.630901   32.095852   
12651      A 2012-04-03   32.002861   32.296139   31.802574   32.067238   
12652      A 2012-04-04   31.716738   31.795422   31.008583   31.287554   
12653      A 2012-04-05   31.230330   32.174534   31.158798   32.024319   
...      ...        ...         ...         ...         ...         ...   
15675      A 2024-04-11  145.649994  145.860001  143.669998  145.000000   
15676      A 2024-04-12  143.589996  144.660004  140.259995  140.729996   
15677      A 2024-04-15  142.309998  143.250000  139.020004  140.220001   
15678      A 2024-04-16  140.279999  140.360001  136.630005  136.800003   
15679      A 2024-04-17  137.240005  137.460007  132.869995  134.550003   

        Adj Close     Volume Symbol_AAL  Open_AAL  High_AAL  Low_AAL  \
12649   28.679214  3246715.0        AAL      7.91      7.91     7.56   
12650   28.911177  3161717.0        AAL      7.59      7.71     7.41   
12651   28.885399  3852748.0        AAL      7.49      7.78     7.48   
12652   28.183073  3342338.0        AAL      7.88      7.97     7.81   
12653   28.846741  6933381.0        AAL      7.84      8.04     7.74   
...           ...        ...        ...       ...       ...      ...   
15675  145.000000   720100.0        AAL     13.44     13.72    13.30   
15676  140.729996  1124500.0        AAL     13.24     13.30    13.02   
15677  140.220001  1506000.0        AAL     13.28     13.47    12.90   
15678  136.800003  1345700.0        AAL     12.95     13.14    12.72   
15679  134.550003  2084100.0        AAL     13.45     13.97    13.38   

       Close_AAL  Adj Close_AAL  Volume_AAL Symbol_AAPL   Open_AAPL  \
12649       7.59       7.155407   6739200.0        AAPL   21.741785   
12650       7.47       7.042280   7355100.0        AAPL   21.493929   
12651       7.74       7.296820   6951000.0        AAPL   22.403570   
12652       7.86       7.409948   8786400.0        AAPL   22.298214   
12653       7.78       7.334528   4947900.0        AAPL   22.392143   
...          ...            ...         ...         ...         ...   
15675      13.62      13.620000  27814200.0        AAPL  168.339996   
15676      13.15      13.150000  35529200.0        AAPL  174.259995   
15677      12.94      12.940000  27451700.0        AAPL  175.360001   
15678      13.03      13.030000  26477200.0        AAPL  171.750000   
15679      13.89      13.890000  52414800.0        AAPL  169.610001   

        High_AAPL    Low_AAPL  Close_AAPL  Adj Close_AAPL  Volume_AAPL  \
12649   21.805714   21.355000   21.412500       18.127813  731038000.0   
12650   22.098928   21.442142   22.093929       18.704712  598351600.0   
12651   22.578930   22.232500   22.475714       19.027937  834559600.0   
12652   22.352142   22.035713   22.296785       18.876444  572980800.0   
12653   22.666430   22.264286   22.631430       19.159750  641298000.0   
...           ...         ...         ...             ...          ...   
15675  175.460007  168.160004  175.039993      175.039993   91070300.0   
15676  178.360001  174.210007  176.550003      176.550003  101593300.0   
15677  176.630005  172.500000  172.690002      172.690002   73531800.0   
15678  173.759995  168.270004  169.380005      169.380005   73711200.0   
15679  170.649994  168.000000  168.000000      168.000000   50901200.0   

      Symbol_ABBV   Open_ABBV   High_ABBV    Low_ABBV  Close_ABBV  \
12649        ABBV   34.919998   35.400002   34.099998   35.119999   
12650        ABBV   34.919998   35.400002   34.099998   35.119999   
12651        ABBV   34.919998   35.400002   34.099998   35.119999   
12652        ABBV   34.919998   35.400002   34.099998   35.119999   
12653        ABBV   34.919998   35.400002   34.099998   35.119999   
...           ...         ...         ...         ...         ...   
15675        AB

In [74]:
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans
import numpy as np

scaler = StandardScaler()
X = test[[col for col in test.columns if 'Date' not in col and 'Symbol' not in col]]
X = scaler.fit_transform(X)

In [80]:
len(X)

3031

In [81]:
new_df = pd.DataFrame(X, columns=[col for col in test.columns if 'Date' not in col and 'Symbol' not in col])
new_df = pd.concat([new_df, test['Date']], axis=1)
new_df

Open      High       Low     Close  Adj Close    Volume  Open_AAL  \
0     -1.070741 -1.076010 -1.077694 -1.075711  -1.080553  0.478529 -1.488977   
1     -1.075073 -1.071724 -1.073834 -1.069468  -1.074994  0.427481 -1.512412   
2     -1.071088 -1.071038 -1.069624 -1.070162  -1.075612  0.842504 -1.519735   
3     -1.078019 -1.083039 -1.089097 -1.089062  -1.092444  0.535959 -1.491174   
4     -1.089803 -1.073953 -1.085413 -1.071202  -1.076538  2.692688 -1.494104   
...         ...       ...       ...       ...        ...       ...       ...   
15675       NaN       NaN       NaN       NaN        NaN       NaN       NaN   
15676       NaN       NaN       NaN       NaN        NaN       NaN       NaN   
15677       NaN       NaN       NaN       NaN        NaN       NaN       NaN   
15678       NaN       NaN       NaN       NaN        NaN       NaN       NaN   
15679       NaN       NaN       NaN       NaN        NaN       NaN       NaN   

       High_AAL   Low_AAL  Close_AAL  Adj Close_AAL  Volume_AAL  Open_AAPL  \
0     -1.507537 -1.495343  -1.510958      -1.552476   -0.541394  -0.865001   
1     -1.522037 -1.506444  -1.519747      -1.561155   -0.517102  -0.869288   
2     -1.516962 -1.501264  -1.499973      -1.541628   -0.533040  -0.853557   
3     -1.503187 -1.476840  -1.491184      -1.532950   -0.460650  -0.855379   
4     -1.498112 -1.482020  -1.497043      -1.538736   -0.612044  -0.853754   
...         ...       ...        ...            ...         ...        ...   
15675       NaN       NaN        NaN            NaN         NaN        NaN   
15676       NaN       NaN        NaN            NaN         NaN        NaN   
15677       NaN       NaN        NaN            NaN         NaN        NaN   
15678       NaN       NaN        NaN            NaN         NaN        NaN   
15679       NaN       NaN        NaN            NaN         NaN        NaN   

       High_AAPL  Low_AAPL  Close_AAPL  Adj Close_AAPL  Volume_AAPL  \
0      -0.867651 -0.867875   -0.870726       -0.883616     3.494017   
1      -0.862635 -0.866352   -0.858953       -0.873738     2.650601   
2      -0.854424 -0.852544   -0.852357       -0.868203     4.152048   
3      -0.858303 -0.855982   -0.855448       -0.870797     2.489333   
4      -0.852927 -0.851989   -0.849667       -0.865946     2.923588   
...          ...       ...         ...             ...          ...   
15675        NaN       NaN         NaN             NaN          NaN   
15676        NaN       NaN         NaN             NaN          NaN   
15677        NaN       NaN         NaN             NaN          NaN   
15678        NaN       NaN         NaN             NaN          NaN   
15679        NaN       NaN         NaN             NaN          NaN   

       Open_ABBV  High_ABBV  Low_ABBV  Close_ABBV  Adj Close_ABBV  \
0      -1.368132  -1.367849 -1.375211   -1.363688        -1.20956   
1      -1.368132  -1.367849 -1.375211   -1.363688        -1.20956   
2      -1.368132  -1.367849 -1.375211   -1.363688        -1.20956   
3      -1.368132  -1.367849 -1.375211   -1.363688        -1.20956   
4      -1.368132  -1.367849 -1.375211   -1.363688        -1.20956   
...          ...        ...       ...         ...             ...   
15675        NaN        NaN       NaN         NaN             NaN   
15676        NaN        NaN       NaN         NaN             NaN   
15677        NaN        NaN       NaN         NaN             NaN   
15678        NaN        NaN       NaN         NaN             NaN   
15679        NaN        NaN       NaN         NaN             NaN   

       Volume_ABBV  Open_ABNB  High_ABNB  Low_ABNB  Close_ABNB  \
0         1.142989   0.103615   0.331759  0.072366    0.078216   
1         1.142989   0.103615   0.331759  0.072366    0.078216   
2         1.142989   0.103615   0.331759  0.072366    0.078216   
3         1.142989   0.103615   0.331759  0.072366    0.078216   
4         1.142989   0.103615   0.331759  0.072366    0.078216   
...            ...        ...      